This is the code for the paper 
# 🔥  HOTTER: Hierarchical Optimal Topic Transport with Explanatory Context Representations 🔥 

## 💥 What is HOTTER for?

 HOTTER is a document meta-distance using contextual embeddings from the language model BERT in combination with an LDA topic model. 
 
 HOTTER is an extension of the [research](https://proceedings.neurips.cc/paper/2019/file/8b5040a8a5baf3e0e67386c2e3a9b903-Paper.pdf) and [code](https://github.com/IBM/HOTT) by Yurochkin et al. on the Hierarchical Optimal Topic Transport (HOTT).

## 💥 Content

With this notebook, you can reproduce the results reported in the [HOTTER paper](https://aclanthology.org/2021.findings-emnlp.418/). You will go through the following steps:

1. Downloading the Datasets
2. Further Pre-Training a BERT Model on the Datasets
3. Extract Embeddings from the BERT Model
4. Preprocessing, Topic Modeling and Contextual Embedding Aggregation
5. HOTT(ER) Distance +  Baseline Calculation





## 🔥 1. Downloading the Datasets

First, we download the datasets from Kusner et al. from this [dropbox](https://www.dropbox.com/sh/nf532hddgdt68ix/AABGLUiPRyXv6UL2YAcHmAFqa?dl=0) to reproduce the process in which the HOTT metric was calculated. In addition, we also need the [raw texts](https://www.dropbox.com/sh/f44z3nt3i5279yt/AACHBs4qiISGPdBjB_aEgDVMa?dl=0) of the datasets which have not been preprocessed yet for a) fine-tuning the BERT model and b) extracting the contextual word embeddings.

In [1]:
# datasets used by HOTT
!mkdir data
!wget -P data "https://www.dropbox.com/sh/nf532hddgdt68ix/AACtd7NIdxXUfrxSvP-OUci4a/20ng2_500-emd_tr_te.mat"
!wget -P data "https://www.dropbox.com/sh/nf532hddgdt68ix/AABNO4w-1T6ozVLCxrRNjCgGa/amazon-emd_tr_te_split.mat"
!wget -P data "https://www.dropbox.com/sh/nf532hddgdt68ix/AAArRFEToUmSJg8G9v120rBQa/bbcsport-emd_tr_te_split.mat"
!wget -P data "https://www.dropbox.com/sh/nf532hddgdt68ix/AABLYdubbTlj5-VgiCNKTTopa/classic-emd_tr_te_split.mat"
!wget -P data "https://www.dropbox.com/sh/nf532hddgdt68ix/AAD31LaD0o04z7YSdxsfmZIca/ohsumed-emd_tr_te_ix.mat"
!wget -P data "https://www.dropbox.com/sh/nf532hddgdt68ix/AAD6gtc0gtB4n7zWwwnuPqrYa/r8-emd_tr_te3.mat"
!wget -P data "https://www.dropbox.com/sh/nf532hddgdt68ix/AABg21VwvpVlEXkAGwf4c3bxa/twitter-emd_tr_te_split.mat"


# corresponding raw documents of these datasets to fine-tune BERT and to extract contextual embeddings
!mkdir data/raw_data
!wget -P data/raw_data "https://www.dropbox.com/sh/f44z3nt3i5279yt/AABd4kiMVyKheozC57f_P7aVa/20ng-test-all-terms.txt"
!wget -P data/raw_data "https://www.dropbox.com/sh/f44z3nt3i5279yt/AADXmEvK3nLmTnAiOuQS4oS9a/20ng-train-all-terms.txt"
!wget -P data/raw_data "https://www.dropbox.com/sh/f44z3nt3i5279yt/AABarLseJpwx_0VbP8d2pbNVa/all_amazon_by_line.txt"
!wget -P data/raw_data "https://www.dropbox.com/sh/f44z3nt3i5279yt/AAD0yJEOwF158GbkB57fIS98a/all_classic.txt"
!wget -P data/raw_data "https://www.dropbox.com/sh/f44z3nt3i5279yt/AAAWKcvgigwi6FRCZronseB2a/bbsport_by_sentence.txt"
!wget -P data/raw_data "https://www.dropbox.com/sh/f44z3nt3i5279yt/AACXiE1JCHqHzyBrhmIphi_Wa/test_ohsumed_by_sentence.txt"
!wget -P data/raw_data "https://www.dropbox.com/sh/f44z3nt3i5279yt/AACvA-yfzsAilFyeorHdTIz4a/train_ohsumed_by_sentence.txt"
!wget -P data/raw_data "https://www.dropbox.com/sh/f44z3nt3i5279yt/AADTtNIktX-CqBYR2xR0LAPea/all_twitter_by_line.txt"
# last time we tested the download, the reuters data was not available
!wget -P data/raw_data "https://www.cs.umb.edu/~smimarog/textmining/datasets/r8-train-all-terms.txt"
!wget -P data/raw_data "https://www.cs.umb.edu/~smimarog/textmining/datasets/r8-test-all-terms.txt"


mkdir: cannot create directory ‘data’: File exists
--2021-11-11 23:45:06--  https://www.dropbox.com/sh/nf532hddgdt68ix/AACtd7NIdxXUfrxSvP-OUci4a/20ng2_500-emd_tr_te.mat
Resolving www.dropbox.com (www.dropbox.com)... 2620:100:6027:18::a27d:4812, 162.125.66.18
Connecting to www.dropbox.com (www.dropbox.com)|2620:100:6027:18::a27d:4812|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /sh/raw/nf532hddgdt68ix/AACtd7NIdxXUfrxSvP-OUci4a/20ng2_500-emd_tr_te.mat [following]
--2021-11-11 23:45:06--  https://www.dropbox.com/sh/raw/nf532hddgdt68ix/AACtd7NIdxXUfrxSvP-OUci4a/20ng2_500-emd_tr_te.mat
Reusing existing connection to [www.dropbox.com]:443.
HTTP request sent, awaiting response... 302 Found
Location: https://ucf72b4e5401e281e56a3eb83fd2.dl.dropboxusercontent.com/cd/0/inline/BZz6CGBu4RjT1MqbnppuZgbWipCF454ynTqRlcsEVSpRC8tRKAkjyz8BzAjHwDIdsTN_aBS3kgyIBH_ocFhae82mphU8S6Q89PAToRlOlHklGzT2twqLmvkvSBFhk0YtdmwKHbTu3fNh5PSeGxIgVvSa/file# [following]
--2021

HTTP request sent, awaiting response... 200 OK
Length: 99661349 (95M) [application/octet-stream]
Saving to: ‘data/bbcsport-emd_tr_te_split.mat’

bbcsport-emd_tr_te_ 100%[===================>]  95,04M  7,55MB/s    in 12s     

2021-11-11 23:49:14 (7,80 MB/s) - ‘data/bbcsport-emd_tr_te_split.mat’ saved [99661349/99661349]

--2021-11-11 23:49:14--  https://www.dropbox.com/sh/nf532hddgdt68ix/AABLYdubbTlj5-VgiCNKTTopa/classic-emd_tr_te_split.mat
Resolving www.dropbox.com (www.dropbox.com)... 2620:100:6027:18::a27d:4812, 162.125.66.18
Connecting to www.dropbox.com (www.dropbox.com)|2620:100:6027:18::a27d:4812|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /sh/raw/nf532hddgdt68ix/AABLYdubbTlj5-VgiCNKTTopa/classic-emd_tr_te_split.mat [following]
--2021-11-11 23:49:15--  https://www.dropbox.com/sh/raw/nf532hddgdt68ix/AABLYdubbTlj5-VgiCNKTTopa/classic-emd_tr_te_split.mat
Reusing existing connection to [www.dropbox.com]:443.
HTTP request sent, awaiting 

HTTP request sent, awaiting response... 301 Moved Permanently
Location: /sh/raw/nf532hddgdt68ix/AABg21VwvpVlEXkAGwf4c3bxa/twitter-emd_tr_te_split.mat [following]
--2021-11-11 23:53:34--  https://www.dropbox.com/sh/raw/nf532hddgdt68ix/AABg21VwvpVlEXkAGwf4c3bxa/twitter-emd_tr_te_split.mat
Reusing existing connection to [www.dropbox.com]:443.
HTTP request sent, awaiting response... 302 Found
Location: https://ucbf4191c6cb329113e75c8f84ae.dl.dropboxusercontent.com/cd/0/inline/BZxxBe85tJC6EU4J65RKF_dm9PkJ6ku0aiyLPmY3SKTgs4bjTpBv5gjofTC8hZKpT9oaPGqjppCJlY4unemHm4sNwbXPKGlESMqkw-N8ZKxKRyrhE0Ymar9EXivpkQKZqcXiCCmW-LMU8HM1OMD1xhgh/file# [following]
--2021-11-11 23:53:35--  https://ucbf4191c6cb329113e75c8f84ae.dl.dropboxusercontent.com/cd/0/inline/BZxxBe85tJC6EU4J65RKF_dm9PkJ6ku0aiyLPmY3SKTgs4bjTpBv5gjofTC8hZKpT9oaPGqjppCJlY4unemHm4sNwbXPKGlESMqkw-N8ZKxKRyrhE0Ymar9EXivpkQKZqcXiCCmW-LMU8HM1OMD1xhgh/file
Resolving ucbf4191c6cb329113e75c8f84ae.dl.dropboxusercontent.com (ucbf4191c6cb329113e75c8f84ae

--2021-11-11 23:53:51--  https://www.dropbox.com/sh/f44z3nt3i5279yt/AAD0yJEOwF158GbkB57fIS98a/all_classic.txt
Resolving www.dropbox.com (www.dropbox.com)... 2620:100:6027:18::a27d:4812, 162.125.72.18
Connecting to www.dropbox.com (www.dropbox.com)|2620:100:6027:18::a27d:4812|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /sh/raw/f44z3nt3i5279yt/AAD0yJEOwF158GbkB57fIS98a/all_classic.txt [following]
--2021-11-11 23:55:04--  https://www.dropbox.com/sh/raw/f44z3nt3i5279yt/AAD0yJEOwF158GbkB57fIS98a/all_classic.txt
Reusing existing connection to [www.dropbox.com]:443.
HTTP request sent, awaiting response... 302 Found
Location: https://uc368305e9c7e9d35d3e13e358f5.dl.dropboxusercontent.com/cd/0/inline/BZw0GWdMSqt_lB0dDVAXxwdlhLf6UDKoh49lPmdKcw41ztT56rDzrq8vTNbVzgVUzf-W_iOM--KN5tPDG7OHSpU2Iab4h_VSuF5POcWKd9isjVRQAYGKqvA7HGte5GbPhGvBi0f7eaJ2wHVu6Hsppd2k/file# [following]
--2021-11-11 23:55:05--  https://uc368305e9c7e9d35d3e13e358f5.dl.dropboxuserconte

Resolving uc1dca98fb6fd38e5a2394558764.dl.dropboxusercontent.com (uc1dca98fb6fd38e5a2394558764.dl.dropboxusercontent.com)... 2620:100:6027:15::a27d:480f, 162.125.72.15
Connecting to uc1dca98fb6fd38e5a2394558764.dl.dropboxusercontent.com (uc1dca98fb6fd38e5a2394558764.dl.dropboxusercontent.com)|2620:100:6027:15::a27d:480f|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 277393 (271K) [text/plain]
Saving to: ‘data/raw_data/all_twitter_by_line.txt’

all_twitter_by_line 100%[===================>] 270,89K   751KB/s    in 0,4s    

2021-11-11 23:55:16 (751 KB/s) - ‘data/raw_data/all_twitter_by_line.txt’ saved [277393/277393]

--2021-11-11 23:55:16--  https://www.cs.umb.edu/~smimarog/textmining/datasets/r8-train-all-terms.txt
Resolving www.cs.umb.edu (www.cs.umb.edu)... 158.121.106.224
Connecting to www.cs.umb.edu (www.cs.umb.edu)|158.121.106.224|:443... connected.
HTTP request sent, awaiting response... 404 Not Found
2021-11-11 23:55:16 ERROR 404: Not Found.

--2021-1

We also clone the BERT repository

In [2]:
! git clone https://github.com/google-research/bert

Cloning into 'bert'...
remote: Enumerating objects: 340, done.
remote: Total 340 (delta 0), reused 0 (delta 0), pack-reused 340
Receiving objects: 100% (340/340), 328.28 KiB | 7.14 MiB/s, done.
Resolving deltas: 100% (182/182), done.


## 🔥 2. Further Pre-Training a BERT Model on the Datasets

This step of adjusting the BERT language model to the dataset is optional as it slightly improves results.

In [1]:
!git clone https://github.com/deepset-ai/FARM.git
%cd FARM
!pip install -r requirements.txt
!pip install --editable .
%cd ..
!pip install sentence_splitter

fatal: destination path 'FARM' already exists and is not an empty directory.
/home/sabine/Desktop/hotter_code/FARM
  Using cached Werkzeug-0.16.1-py2.py3-none-any.whl (327 kB)


  Attempting uninstall: Werkzeug
    Found existing installation: Werkzeug 1.0.1
    Uninstalling Werkzeug-1.0.1:
      Successfully uninstalled Werkzeug-1.0.1
Obtaining file:///home/sabine/Desktop/hotter_code/FARM


  Attempting uninstall: farm
    Found existing installation: farm 0.8.1-snapshot
    Uninstalling farm-0.8.1-snapshot:
      Successfully uninstalled farm-0.8.1-snapshot
  Running setup.py develop for farm
/home/sabine/Desktop/hotter_code


In [1]:
import os
import logging
from pathlib import Path
import torch
from farm.data_handler.data_silo import DataSilo
from farm.data_handler.processor import BertStyleLMProcessor
from farm.modeling.adaptive_model import AdaptiveModel
from farm.modeling.language_model import LanguageModel
from farm.modeling.prediction_head import BertLMHead, NextSentenceHead
from farm.modeling.tokenization import Tokenizer
from farm.train import Trainer
from farm.modeling.optimization import initialize_optimizer
import re
from FARM.farm.utils import set_all_seeds, initialize_device_settings
import csv
from sentence_splitter import SentenceSplitter, split_text_into_sentences
import sys
csv.field_size_limit(sys.maxsize)
import traceback





/home/sabine/anaconda3/lib/python3.8/site-packages/torchaudio/backend/utils.py:53: UserWarning: "sox" backend is being deprecated. The default backend will be changed to "sox_io" backend in 0.8.0 and "sox" backend will be removed in 0.9.0. Please migrate to "sox_io" backend. Please refer to https://github.com/pytorch/audio/issues/903 for the detail.
  warnings.warn(
11/12/2021 01:45:29 - INFO - farm.modeling.prediction_head -   Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex .


### 💥 Select Dataset

Set the dataset you want to fine-tune a BERT model on. When the raw data is split by sentence, set the by_sent flag to True.


In [3]:
raw="./data/raw_data/bbsport_by_sentence.txt"
by_sent=True

In [10]:
def lm_finetuning():
    logging.basicConfig(
        format="%(asctime)s - %(levelname)s - %(name)s -   %(message)s",
        datefmt="%m/%d/%Y %H:%M:%S",
        level=logging.INFO,
    )

    set_all_seeds(seed=42)

    ##########################
    ########## Settings
    ##########################
    device, n_gpu = initialize_device_settings(use_cuda=False)
    n_epochs = 1
    batch_size = 32
    evaluate_every = 30
    lang_model = "bert-base-uncased"
    do_lower_case = False
    next_sent_pred_style = "bert-style"

    # 1.Create a tokenizer
    tokenizer = Tokenizer.load(
        pretrained_model_name_or_path=lang_model, do_lower_case=do_lower_case
    )

    # 2. Create a DataProcessor that handles all the conversion from raw text into a pytorch Dataset
    processor = BertStyleLMProcessor(
        data_dir=Path("."),
        train_filename="train.txt",
        test_filename="test.txt",
        dev_filename="dev.txt",
        tokenizer=tokenizer,
        max_seq_len=512,
        max_docs=3000000, # We have set max_docs to 20 to speed up data processing
        next_sent_pred=False,
        next_sent_pred_style=next_sent_pred_style
    )

    # 3. Create a DataSilo that loads several datasets (train/dev/test), provides DataLoaders for them and calculates a few descriptive statistics of our datasets
    data_silo = DataSilo(processor=processor, batch_size=batch_size ,caching=True)#, max_multiprocessing_chunksize=3)

    # 4. Create an AdaptiveModel
    # a) which consists of a pretrained language model as a basis
    language_model = LanguageModel.load(lang_model)
    # b) and *two* prediction heads on top that are suited for our task => Language Model finetuning
    lm_prediction_head = BertLMHead.load(lang_model)
    next_sentence_head = NextSentenceHead.load(lang_model)

    model = AdaptiveModel(
        language_model=language_model,
        prediction_heads=[lm_prediction_head, next_sentence_head],
        embeds_dropout_prob=0.1,
        lm_output_types=["per_token", "per_sequence"],
        device=device,
    )

    # 5. Create an optimizer
    model, optimizer, lr_schedule = initialize_optimizer(
        model=model,
        learning_rate=2e-5,
        device=device,
        n_batches=len(data_silo.loaders["train"]),
        n_epochs=n_epochs,
        grad_acc_steps=2,
    )

    # 6. Feed everything to the Trainer, which keeps care of growing our model into powerful plant and evaluates it from time to time
    trainer = Trainer.create_or_load_checkpoint(      
        model=model,
        optimizer=optimizer,
        data_silo=data_silo,
        epochs=n_epochs,
        n_gpu=n_gpu,
        lr_schedule=lr_schedule,
        evaluate_every=evaluate_every,
        device=device,
        grad_acc_steps=2,
        checkpoint_on_sigterm=True,
        checkpoint_every=200,
        checkpoint_root_dir=Path("."),
        resume_from_checkpoint="latest")
    # 7. Let it grow! Watch the tracked metrics live on the public mlflow server: https:/public-mlflow.deepset.ai
   # 
  
    trainer.train()
    # 8. Hooray! You have a model. Store it:
    save_dir = Path(".")
    model.save(save_dir)
    processor.save(save_dir)

### 💥 Further pre-train
Now that the model is specified, we can run the code for training the model on our chosen dataset. In case you get an out of memory error, you may want to set the above batch size to a smaller value or switch entirely to CPU. Hint: For this you have to specify use_cuda=False above and torch.device("cpu") below. You can also entirely skip this step in case you do not want to use a further pre-trained BERT model.

In [11]:
try:
        
        splitter = SentenceSplitter(language='en')
        data=[]
        txt_file=open(raw, "r", encoding='latin1')
        print("going through all data...")
        if not by_sent:
            for i, line in enumerate(txt_file.readlines()):
                if i%100==0:
                    print(i)
                data1=[]
                cols = line.split('\t')
                doc=(re.sub("[\r\n]+", "",cols[1]))
                sentences= splitter.split(text=doc)
                for text in sentences:
                    n = 511
                    
                    words = iter(text.split())
                    lines, current = [], next(words)
                    for word in words:
                        if len(current) + 1 + len(word) > n:
                            lines.append(current)
                            current = word
                        else:
                            current += " " + word
                    lines.append(current)  
                           
                    data1.append(("\n").join(lines) )           
                data.append(("\n").join(data1) )
                            
        else:
            sentences=[]
            doc_count=0
            for i, line in enumerate(txt_file.readlines()):
                cols = line.split('\t')
                if doc_count==int(cols[1]):
                    sentences.append(re.sub("[\r\n]+", "",cols[2]))
                else:
                    data1=[]
                    for v, text in enumerate(sentences):
                            
                            #print(v)
                            #print(text)
                            n = 511
                            if not re.match("\s+", text) :
                                words = iter(text.split())
                                
                                lines, current = [], next(words)
                                for word in words:
                                    if len(current) + 1 + len(word) > n:
                                        lines.append(current)
                                        current = word
                                    else:
                                        current += " " + word
                                lines.append(current)  
                                       
                                data1.append(("\n").join(lines) )
                    
                    data.append(("\n").join(data1))
                    sentences=[]
                    sentences.append(cols[2])
                    doc_count+=1  
      
        print("data sample")
        print(len(data))
        traininstances=int(len(data)*0.7)
        devinstances=int(len(data)*0.2)+traininstances
        text=("\n\n").join(data[:traininstances])
        devtext=("\n\n").join(data[traininstances:devinstances])
        testtext=("\n\n").join(data[devinstances:])
        print(len(text))
        with open("train.txt", "w", encoding="utf-8") as trainfile: 
            trainfile.write(text)
        with open("dev.txt", "w", encoding="utf-8") as devfile:
            devfile.write(devtext)
        with open("test.txt", "w", encoding="utf-8") as testfile:
            testfile.write(testtext)
        print(str("Cuda status: " +str(torch.cuda.is_available())))
        device = torch.device("cpu")#"cuda" if torch.cuda.is_available() else "cpu") 
        print("Devices available: {}".format(device))
        lm_finetuning()
except Exception as e:
        print(e)
        print(traceback.print_exc())


## 🔥 3. Extract Embeddings from the BERT Model
Here you either insert the model which you further pre-trained or standard models, such as bert-base-uncased. By adjusting the gpu, seq_length and num_processes parameters, you can ensure that the model runs efficiently on your machine.

In [6]:

import numpy as np
import re
import pickle as pkl
from farm.infer import Inferencer
logger = logging.getLogger(__name__)
logger.setLevel(logging.ERROR)

#location of the fine-tuned model
ft="."


def map_raw(raw, by_sent):
    # this is for utf-8 encoding
    em=[]
    try:
        if by_sent:
            #raw_dict={}
            #cont_emb={}
            num_lines=sum(1 for line in open(raw, encoding="latin1"))
            z=open(raw, "r", encoding='latin1')
            doc_count=0
            sentences=[]
            #inferenced_model = Inferencer.load(ft, extraction_strategy="per_token", extraction_layer=-1, task_type="embeddings", gpu=False, max_seq_len=512, num_processes=5, disable_tqdm=True)
            inferenced_model = Inferencer.load("bert-base-uncased", extraction_strategy="per_token", extraction_layer=-1, task_type="embeddings", gpu=False, max_seq_len=512, num_processes=1, disable_tqdm=True)

            # the commented code below is for inputs that have sentences as 
            # the second column and where the document id is the first column 
            # (we start counting at 0)
            for i, line in enumerate(list(z.readlines())):
                articles=[]
                cols = line.split('\t')
                if doc_count==int(cols[1]):
                    sentences.append(re.sub("[\r\n]+", "",cols[2]))
                else:
                    #sentences=[" ".join(sentences)]
                    for s in sentences:
                        articles.append({'text': s})
                    result = inferenced_model.inference_from_dicts(articles)
                    #cont_emb[doc_count]=result
                    em.append(result)
                   
        
                    #print(result)
                    #input()
                    #print(cont_emb[doc_count])
                    print(str(str(i)+ " / " +str(num_lines)))
                    sentences=[]
                    sentences.append(cols[2])
                    doc_count+=1  
            #to get the last line too
            else:
                articles=[]
                sentences.append(cols[2])
                for s in sentences:
                    articles.append({'text': s})

                result = inferenced_model.inference_from_dicts(articles)
                em.append(result)
                print(doc_count)
                sentences=[]
            z.close()
            return em
                
            z.close()
        else:
            splitter = SentenceSplitter(language='en')
            num_lines=sum(1 for line in open(raw, encoding="latin1"))
            z=open(raw, "r", encoding='latin1')
           
            #inferenced_model = Inferencer.load(ft, extraction_strategy="per_token", extraction_layer=-1, task_type="embeddings", gpu=False, max_seq_len=512, num_processes=5, disable_tqdm=True)
            inferenced_model = Inferencer.load("bert-base-uncased", extraction_strategy="per_token", extraction_layer=-1, task_type="embeddings", gpu=False, max_seq_len=512, num_processes=1, disable_tqdm=True)

            for i, line in enumerate(list(z.readlines())):
             
                articles=[]
                cols = line.split('\t')
                doc=(re.sub("[\r\n]+", "",cols[1]))
                sentences= splitter.split(text=doc)
                for text in sentences:
                    
                    articles.append({'text': text})
                    
                    result = inferenced_model.inference_from_dicts(articles)
                  
                    em.append(result)
                   
                    print(str(str(i)+ " / " +str(num_lines)))
                    
            #to get the last line too
            else:
                articles=[]
                sentences= splitter.split(text=doc)
                for text in sentences:
                    articles.append({'text': text})
                    
                    result = inferenced_model.inference_from_dicts(articles)
                  
                    em.append(result)
                   
                    print(str(str(i)+ " / " +str(num_lines)))
            z.close()
            return em
                
            
    except Exception as E:
            print(E)
            print(traceback.print_exc())
            


if not os.path.exists(ft+"/%s_emb.pkl"%raw):
    
    embs=map_raw(ft+"/%s"%raw,by_sent)
    with open(ft+"/%s_emb.pkl"%os.path.splitext(raw)[0],"wb") as handle:
        pkl.dump(embs, handle)
    print("Done with embedding file.")


11/12/2021 01:47:43 - INFO - farm.utils -   Using device: CPU 
11/12/2021 01:47:43 - INFO - farm.utils -   Number of GPUs: 0
11/12/2021 01:47:43 - INFO - farm.utils -   Distributed Training: False
11/12/2021 01:47:43 - INFO - farm.utils -   Automatic Mixed Precision: None
11/12/2021 01:47:43 - INFO - farm.modeling.language_model -   
11/12/2021 01:47:43 - INFO - farm.modeling.language_model -   LOADING MODEL
11/12/2021 01:47:43 - INFO - farm.modeling.language_model -   =============
11/12/2021 01:47:43 - INFO - farm.modeling.language_model -   Could not find bert-base-uncased locally.
11/12/2021 01:47:43 - INFO - farm.modeling.language_model -   Looking on Transformers Model Hub (in local cache and online)...
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 

0 / 12941


11/12/2021 01:47:58 - INFO - farm.data_handler.processor -   *** Show 1 random examples ***
11/12/2021 01:47:58 - INFO - farm.data_handler.processor -   

      .--.        _____                       _      
    .'_\/_'.     / ____|                     | |     
    '. /\ .'    | (___   __ _ _ __ ___  _ __ | | ___ 
      "||"       \___ \ / _` | '_ ` _ \| '_ \| |/ _ \ 
       || /\     ____) | (_| | | | | | | |_) | |  __/
    /\ ||//\)   |_____/ \__,_|_| |_| |_| .__/|_|\___|
   (/\||/                             |_|           
______\||/___________________________________________                     

ID: None
Clear Text: 
 	text:   greene crossed the line just number seconds behind gatlin  who won in number seconds in one of the closest and fastest sprints of all time 
Tokenized: 
 	None
Features: 
 	input_ids: [101, 11006, 4625, 1996, 2240, 2074, 2193, 3823, 2369, 11721, 19646, 2378, 2040, 2180, 1999, 2193, 3823, 1999, 2028, 1997, 1996, 7541, 1998, 7915, 9043, 2015, 1997, 2035, 2051,

1 / 12941


11/12/2021 01:48:09 - INFO - farm.data_handler.processor -   *** Show 1 random examples ***
11/12/2021 01:48:09 - INFO - farm.data_handler.processor -   

      .--.        _____                       _      
    .'_\/_'.     / ____|                     | |     
    '. /\ .'    | (___   __ _ _ __ ___  _ __ | | ___ 
      "||"       \___ \ / _` | '_ ` _ \| '_ \| |/ _ \ 
       || /\     ____) | (_| | | | | | | |_) | |  __/
    /\ ||//\)   |_____/ \__,_|_| |_| |_| .__/|_|\___|
   (/\||/                             |_|           
______\||/___________________________________________                     

ID: None
Clear Text: 
 	text: it was also agreed that a programme to  de mystify  the issue to athletes  the public and the media was a priority 
Tokenized: 
 	None
Features: 
 	input_ids: [101, 2009, 2001, 2036, 3530, 2008, 1037, 4746, 2000, 2139, 2026, 16643, 12031, 1996, 3277, 2000, 7576, 1996, 2270, 1998, 1996, 2865, 2001, 1037, 9470, 102, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

...

733 / 12941


11/12/2021 03:15:22 - INFO - farm.data_handler.processor -   *** Show 1 random examples ***
11/12/2021 03:15:22 - INFO - farm.data_handler.processor -   

      .--.        _____                       _      
    .'_\/_'.     / ____|                     | |     
    '. /\ .'    | (___   __ _ _ __ ___  _ __ | | ___ 
      "||"       \___ \ / _` | '_ ` _ \| '_ \| |/ _ \ 
       || /\     ____) | (_| | | | | | | |_) | |  __/
    /\ ||//\)   |_____/ \__,_|_| |_| |_| .__/|_|\___|
   (/\||/                             |_|           
______\||/___________________________________________                     

ID: None
Clear Text: 
 	text:  i will try not to think about what happened but i don t think it will have any effect on the british team s concentration 
Tokenized: 
 	None
Features: 
 	input_ids: [101, 1045, 2097, 3046, 2025, 2000, 2228, 2055, 2054, 3047, 2021, 1045, 2123, 1056, 2228, 2009, 2097, 2031, 2151, 3466, 2006, 1996, 2329, 2136, 1055, 6693, 102, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

734 / 12941


11/12/2021 03:15:27 - INFO - farm.data_handler.processor -   *** Show 1 random examples ***
11/12/2021 03:15:27 - INFO - farm.data_handler.processor -   

      .--.        _____                       _      
    .'_\/_'.     / ____|                     | |     
    '. /\ .'    | (___   __ _ _ __ ___  _ __ | | ___ 
      "||"       \___ \ / _` | '_ ` _ \| '_ \| |/ _ \ 
       || /\     ____) | (_| | | | | | | |_) | |  __/
    /\ ||//\)   |_____/ \__,_|_| |_| |_| .__/|_|\___|
   (/\||/                             |_|           
______\||/___________________________________________                     

ID: None
Clear Text: 
 	text:   

Tokenized: 
 	None
Features: 
 	input_ids: [101, 102, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

735 / 12941
736
Done with embedding file.


## 🔥 4. Preprocessing, Topic Modeling and Contextual Embedding Aggregation

Here, we stick for most part to the original HOTT code. In this step, the vocabulary is created and it is ensured that there is no out of vocabulary problem by looking up the words from pre-trained Word2Vec or GloVe embeddings and restricting the overall vocabulary for LDA on these words.

Make sure you select the correct dataset below

In [12]:
!pip install lda
!pip install pot

# download glove vectors
!wget -P data https://nlp.stanford.edu/data/glove.6B.zip


--2021-11-12 09:01:04--  https://nlp.stanford.edu/data/glove.6B.zip
Resolving nlp.stanford.edu (nlp.stanford.edu)... 171.64.67.140
Connecting to nlp.stanford.edu (nlp.stanford.edu)|171.64.67.140|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: http://downloads.cs.stanford.edu/nlp/data/glove.6B.zip [following]
--2021-11-12 09:01:05--  http://downloads.cs.stanford.edu/nlp/data/glove.6B.zip
Resolving downloads.cs.stanford.edu (downloads.cs.stanford.edu)... 171.64.64.22
Connecting to downloads.cs.stanford.edu (downloads.cs.stanford.edu)|171.64.64.22|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 862182613 (822M) [application/zip]
Saving to: ‘data/glove.6B.zip’

glove.6B.zip        100%[===================>] 822,24M  3,37MB/s    in 4m 19s  

2021-11-12 09:05:24 (3,18 MB/s) - ‘data/glove.6B.zip’ saved [862182613/862182613]



In [13]:
!mkdir data/glove.6B
!unzip data/glove.6B.zip -d data/glove.6B

Archive:  data/glove.6B.zip
  inflating: glove.6B.50d.txt        
  inflating: glove.6B.100d.txt       
  inflating: glove.6B.200d.txt       
  inflating: glove.6B.300d.txt       


In [4]:
from sklearn.preprocessing import normalize
from sklearn.model_selection import train_test_split
import time
import lda
import numpy as np
from knn_classifier import knn
import distances
import hott
import pickle
import lda
import os
import csv
import re
import sys
from collections import defaultdict
from hott import sparse_ot
from sklearn.metrics.pairwise import euclidean_distances
from scipy.io import loadmat
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer
from bert import tokenization
data_path = 'data/'

data_name = 'bbcsport-emd_tr_te_split.mat'
raw_data_name='bbsport_by_sentence.txt'
train_test_dataset=False
by_sentence=True

embeddings_path = './data/glove.6B/glove.6B.300d.txt'

In [5]:

''' this function maps the tokens used in the topic model to the tokens 
 from the contextual word embeddings
 obtained by the BERT tokenizer'''
 
def check_previous(i, x, z):
    m=z[i-1]+x.strip("##")
    if m.startswith("##"):
        m=check_previous(i-1,m,z)
    return m

 
def sub_aggregate(i,g,embs):
    # helper function used to average the embedding values of multi part subwords from BERT
    em=[]
    for x in range(i,g+1):
        em.append(embs[x])
    if len(em)>1:
        return np.mean(np.asarray(em), axis=0)
    else:
        return np.asarray(em[0])
    
 
def pre_aggregate(c_embeddings):
    # this function is the first step for resolving BERT subwords into the topic model's tokens
    todo=str(len(c_embeddings))
    
    word_emb = defaultdict(list)
    word_doc = defaultdict(list)
    doc_word = defaultdict(list)
    doc_emb ={}
    try:
      
            for d in range(0,len(c_embeddings)):
                print(str(str(d)+"\\"+todo))
                for c in range(len(c_embeddings[d])):
                    if isinstance(c_embeddings[d][c]["context"], list):
                        docwords= c_embeddings[d][c]["context"]
                    else:
                         docwords= c_embeddings[d][c]["context"].split()
                    for i in range(1,len(docwords)):
                        v=docwords[i]
                        if v.startswith("##") and not docwords[i-1].startswith("##"):
                            u=str(docwords[i-1]+v.lstrip("##"))
                            for g in range(i, len(docwords)):
                                if len(docwords)>g+1:
                                    if docwords[g+1].startswith("##"):
                                        u=u+str(docwords[g+1].lstrip("##"))
                                    else:
                                        word_emb[u].append(sub_aggregate(i-1,g, c_embeddings[d][c]["vec"]))
                                        word_doc[u].append(d)
                                        doc_emb[d]=np.mean(list(c_embeddings[d][c]["vec"]), axis=0)
                                        doc_word[d].append(docwords)
                                        break
                        elif len(docwords)>i+1:
                            if docwords[i+1].startswith("##"):
                                continue
                            if not docwords[i+1].startswith("##"):
                                word_emb[v].append(c_embeddings[d][c]["vec"][i])
                                word_doc[v].append(d)
                                doc_emb[d]=np.mean(list(c_embeddings[d][c]["vec"]), axis=0)
                                doc_word[d].append(docwords)
                                                        
                        else:
                            if len(docwords)==i and not docwords[i].startswith("##"):
                                word_emb[v].append(c_embeddings[d][c]["vec"][i])
                                word_doc[v].append(d)
                                doc_emb[d]=np.mean(list(c_embeddings[d][c]["vec"]), axis=0)
                                doc_word[d].append(docwords)   
       
    except Exception as E:
                    print("error")
                    print(E)
                    print(d)
                    print(v)
                    traceback.print_exc()
    print("reached the end")                
    return [word_emb, word_doc, doc_word, doc_emb]

def map_to_emb(o,w, word_emb, word_doc, doc_word, doc_emb ,m_topic_wdocs):
    """"uses the output of the pre-aggregate function to come up with the final word embeddings"""
    #print(o)
    print(w)
    try:
        semb=[]
        memb=[]
        msemb=[]
        emb=[]
        stemmer=SnowballStemmer("english")
        print(len(word_doc.keys()))
        for g,v in enumerate(word_doc.keys()):
    
                if v.lower()==w:
                    if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                        semb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                    else:
                        semb.append(np.asarray(word_emb[v],dtype=float))
                    #print("semb 1")
                
                    for d in word_doc[v]:
                        emb.append(np.asarray(doc_emb[d],dtype=float))
                        if w in m_topic_wdocs:
                           
                            for b in m_topic_wdocs[w]: 
                                if b==d:
                                    #for d in word_doc[v]:
                                    memb.append(doc_emb[d])
                                    if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                        msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                                    else:
                                        msemb.append(np.asarray(word_emb[v],dtype=float))
                           
                        else:
                            #for d in word_doc[v]:
                            memb.append(doc_emb[d])
                            if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                            else:
                                msemb.append(np.asarray(word_emb[v],dtype=float))
        else:
            for g,v in enumerate(word_doc.keys()):
              if v.lower().startswith(w):
                    if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                        semb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                    else:
                        semb.append(np.asarray(word_emb[v],dtype=float))
                    #print("semb 2")
                   
                    for d in word_doc[v]:
                        emb.append(np.asarray(doc_emb[d],dtype=float))
                        if w in m_topic_wdocs:
                           
                            for b in m_topic_wdocs[w]: 
                                if b==d:
                                    #for d in word_doc[v]:
                                    memb.append(doc_emb[d])
                                    if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                        msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                                    else:
                                        msemb.append(np.asarray(word_emb[v],dtype=float))
                           
                        else:
                            for d in word_doc[v]:
                                memb.append(doc_emb[d])
                            if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                            else:
                                msemb.append(np.asarray(word_emb[v],dtype=float))
            else:
                for g,v in enumerate(word_doc.keys()):
                  j=stemmer.stem(v)
                  if j.lower().startswith(w):
                        if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                            semb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                        else:
                            semb.append(np.asarray(word_emb[v],dtype=float))
                        #print("semb 3")
                        
                        
                        for d in word_doc[v]:
                            emb.append(np.asarray(doc_emb[d],dtype=float))
                            if w in m_topic_wdocs:
                               
                                for b in m_topic_wdocs[w]: 
                                    if b==d:
                                        #for d in word_doc[v]:
                                        memb.append(doc_emb[d])
                                        if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                            msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                                        else:
                                            msemb.append(np.asarray(word_emb[v],dtype=float))
                               
                            else:
                                #or d in word_doc[v]:
                                memb.append(doc_emb[d])
                                if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                    msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                                else:
                                    msemb.append(np.asarray(word_emb[v],dtype=float))
                
        if len(emb)>1 and len(emb)<=300000000:
            #print(emb)
            #input()
            emb=np.mean(emb, axis=0)
        elif len(emb)>1 and len(emb)>300000000:
            emb=emb[:300000000]
            emb=np.mean(emb, axis=0)
            #print(emb)
            #print("emb after mean")
            #input()
        if len(semb)>1 and len(semb)<=300000000:

            #print(semb)
            #input()
            semb=np.mean(semb, axis=0)
        elif len(semb)>1 and len(semb)>300000000:
            semb=semb[:300000000]
            semb=np.mean(semb, axis=0)

            #print(semb)
            #print("semb after mean")
            #input()
        if len(memb)>1 and len(memb)<=300000000:

            memb=np.mean(memb, axis=0)

        elif len(memb)>1 and len(memb)>300000000:
            memb=memb[:300000000]
            memb=np.mean(memb, axis=0)

        if len(msemb)>1 and len(msemb)<=300000000:

            msemb=np.mean(msemb, axis=0)
        elif len(msemb)>1 and len(msemb)>300000000:
            msemb=msemb[:300000000]
            msemb=np.mean(msemb, axis=0)

        if np.asarray(emb).shape==(1,768):
            emb=np.asarray(emb).reshape(768,)
        if np.asarray(semb).shape==(1,768):
            semb=np.asarray(semb).reshape(768,)
        if np.asarray(memb).shape==(1,768):
            memb=np.asarray(memb).reshape(768,)
        if np.asarray(msemb).shape==(1,768):
            msemb=np.asarray(msemb).reshape(768,)
        if np.asarray(emb).shape==(768,) and np.asarray(semb).shape==(768,) and np.asarray(memb).shape==(768,) and np.asarray(msemb).shape==(768,):
            return [w, np.asarray(emb), np.asarray(semb), np.asarray(memb), np.asarray(msemb)]
        else:
            
            
            print("Word could not be resolved in BERT tokens")
            #print(w)
            should_restart = True
            z=w
            while should_restart:
                should_restart = False
                
                z = z[:-1]
                #print(np.asarray(emb).shape)
                #print(np.asarray(semb).shape)
                #print(np.asarray(msemb).shape)
                #print(np.asarray(memb).shape)
                #print(semb)
                #print(m_topic_wdocs[w])
                semb=list(semb)
                emb=list(emb)
                memb=list(memb)
                msemb=list(msemb)
                print(z)
                #input()
                for g,v in enumerate(word_doc.keys()):
                    if v.lower()==z:
                        if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                            semb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                        else:
                            semb.append(np.asarray(word_emb[v],dtype=float))
                        #print("semb 4")
                       
                        for d in word_doc[v]:
                            emb.append(np.asarray(doc_emb[d],dtype=float))
                            if w in m_topic_wdocs:
                               
                                for b in m_topic_wdocs[w]: 
                                    if b==d:
                                        #for d in word_doc[v]:
                                        memb.append(doc_emb[d])
                                        if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                            msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                                        else:
                                            msemb.append(np.asarray(word_emb[v],dtype=float))
                                               
                            else:
                                #for d in word_doc[v]:
                                memb.append(doc_emb[d])
                                if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                    msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                                else:
                                    msemb.append(np.asarray(word_emb[v],dtype=float))
                            
                else:
                    for g,v in enumerate(word_doc.keys()):
                      if v.lower().startswith(z):
                            if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                semb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                            else:
                                semb.append(np.asarray(word_emb[v],dtype=float))
                            #print("semb 5")
                      
                            for d in word_doc[v]:
                                emb.append(np.asarray(doc_emb[d],dtype=float))
                                if w in m_topic_wdocs:
                                   
                                    for b in m_topic_wdocs[w]: 
                                        if b==d:
                                            #for d in word_doc[v]:
                                            memb.append(doc_emb[d])
                                            if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                                msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                                            else:
                                                msemb.append(np.asarray(word_emb[v],dtype=float))
                                   
                                    else:
                                        memb.append(doc_emb[d])
                                        if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                            msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                                        else:
                                            msemb.append(np.asarray(word_emb[v],dtype=float))
                                else:
                                  
                                    memb.append(doc_emb[d])
                                    if np.asarray(word_emb[v],dtype=float).shape!=(768,):
                                        msemb.append(np.mean(np.asarray(word_emb[v],dtype=float), axis=0))
                                    else:
                                        msemb.append(np.asarray(word_emb[v],dtype=float))
                #print(memb)
                #print(len(memb))
                print(np.asarray(emb).shape)
                print(np.asarray(semb).shape)
                print(np.asarray(memb).shape)
                print(np.asarray(msemb).shape)
                #input()
                if len(emb)>1:
                    emb=np.mean(emb, axis=0)
                if len(semb)>1:
                    semb=np.mean(semb, axis=0)
                if len(memb)>1:
                    memb=np.mean(memb, axis=0)
                if len(msemb)>1:
                    msemb=np.mean(msemb, axis=0)
                if np.asarray(emb).shape==(1,768):
                    emb=np.asarray(emb).reshape(768,)
                if np.asarray(semb).shape==(1,768):
                    semb=np.asarray(semb).reshape(768,)
                if np.asarray(memb).shape==(1,768):
                    memb=np.asarray(memb).reshape(768,)
                if np.asarray(msemb).shape==(1,768):
                    msemb=np.asarray(msemb).reshape(768,)
                if  np.asarray(emb).shape==(768,) and np.asarray(semb).shape==(768,) and np.asarray(memb).shape==(768,) and np.asarray(msemb).shape==(768,):
                    return [w, np.asarray(emb), np.asarray(semb), np.asarray(memb), np.asarray(msemb)]
                else:
                        should_restart=True
    except Exception as e:
        print(e)
        print(traceback.print_exc()) 
 
    
 

def load_wmd_data(path):
    """Load data used in the WMD paper for baselines.
    """
    
    mat_data = loadmat(path, squeeze_me=True, chars_as_strings=True)

    try:
        y = mat_data['Y'].astype(np.int)
    except KeyError:
        y = np.concatenate((mat_data['ytr'].astype(np.int),
                            mat_data['yte'].astype(np.int)))
    try:
        embeddings_of_doc_words = mat_data['X']
    except KeyError:
        embeddings_of_doc_words = np.concatenate((mat_data['xtr'],
                                                  mat_data['xte']))
    try:
        doc_word_counts = mat_data['BOW_X']
    except KeyError:
        doc_word_counts = np.concatenate((mat_data['BOW_xtr'], mat_data['BOW_xte']))
    try:
        doc_words = mat_data['words']
    except KeyError:
        print(mat_data.keys())
        doc_words = np.concatenate((mat_data['words_tr'], mat_data['words_te']))
        
    vocab = []
    embed_vocab = {}
    for d_w, d_e in zip(doc_words, embeddings_of_doc_words):
        if type(d_w) == str:
            d_w = [d_w]
        words = [w for w in d_w if type(w) == str]
        if len(words) == 1:
            d_e = d_e.reshape((-1, 1))
        for i, w in enumerate(words):
            if w not in vocab:
                vocab.append(w)
                embed_vocab[w] = d_e[:, i]
            else:
                if not np.allclose(embed_vocab[w], d_e[:, i]):
                    print('Problem with embeddings')
                    break
    
    bow_data = np.zeros((len(doc_word_counts), len(vocab)),
                        dtype=np.int)
    for doc_idx, (d_w, d_c) in enumerate(zip(doc_words, doc_word_counts)):
        if type(d_w) == str:
            d_w = [d_w]
        words = [w for w in d_w if type(w) == str]
        if len(words) == 1:
            d_c = np.array([d_c])
        words_idx = np.array([vocab.index(w) for w in words])
        bow_data[doc_idx, words_idx] = d_c.astype(np.int)

    return vocab, embed_vocab, bow_data, y, doc_words

def load_20news():
    #20ng is not in kusner's dataset, we need to fetch it elsewhere
    from sklearn.datasets import fetch_20newsgroups
    from sklearn.feature_extraction.text import CountVectorizer
    newsgroups_train = fetch_20newsgroups(subset='train', remove=('headers', 'footers', 'quotes'))
    newsgroups_test = fetch_20newsgroups(subset='test', remove=('headers', 'footers', 'quotes'))
    
    tf_vectorizer = CountVectorizer(max_df=0.95, min_df=5, stop_words='english')
    X_train = tf_vectorizer.fit_transform(newsgroups_train.data)
    vocab = sorted(tf_vectorizer.vocabulary_.items(), key = lambda x: x[1])
    vocab = [v[0] for v in vocab]
    vocab_start = 1520 # removing weird words
    min_doc_length = 20 - 1 # removing short docs
    vocab = vocab[vocab_start:]
    X_train = X_train.toarray()[:,vocab_start:]
    y_train = newsgroups_train.target[X_train.sum(axis=1)>min_doc_length]
    X_train = X_train[X_train.sum(axis=1)>min_doc_length]
    doc_words=newsgroups_train.data + newsgroups_test.data
    X_test = tf_vectorizer.transform(newsgroups_test.data)
    X_test = X_test.toarray()[:,vocab_start:]
    y_test = newsgroups_test.target[X_test.sum(axis=1)>min_doc_length]
    X_test = X_test[X_test.sum(axis=1)>min_doc_length]
    
    X = np.vstack((X_train, X_test)).astype(np.int)
    y = np.concatenate((y_train, y_test))
    

    
    return vocab, X, y,  doc_words



def reduce_vocab(bow_data, vocab, embed_vocab, embed_aggregate='mean'):
    """Reduce vocabulary size by stemming and removing stop words.
    """
    vocab = np.array(vocab)
    short = np.array([len(w) > 2 for w in vocab])
    stop_words = set(stopwords.words('english'))
    stop = np.array([w not in stop_words for w in vocab])
    reduced_vocab = vocab[np.logical_and(short, stop)]
    reduced_bow_data = bow_data[:, np.logical_and(short, stop)]
    stemmer = SnowballStemmer("english")
    stemmed_dict = {}
    stemmed_idx_mapping = {}
    stemmed_vocab = []
    for i, w in enumerate(reduced_vocab):
        stem_w = stemmer.stem(w)
        if stem_w in stemmed_vocab:
            stemmed_dict[stem_w].append(w)
            stemmed_idx_mapping[stemmed_vocab.index(stem_w)].append(i)
        else:
            stemmed_dict[stem_w] = [w]
            stemmed_vocab.append(stem_w)
            stemmed_idx_mapping[stemmed_vocab.index(stem_w)] = [i]

    stemmed_bow_data = np.zeros((bow_data.shape[0], len(stemmed_vocab)),
                                dtype=np.int)
    for i in range(len(stemmed_vocab)):
        stemmed_bow_data[:, i] = reduced_bow_data[:, stemmed_idx_mapping[i]].sum(axis=1).flatten()

    word_counts = stemmed_bow_data.sum(axis=0)
    stemmed_reduced_vocab = np.array(stemmed_vocab)[word_counts > 2].tolist()
    stemmed_reduced_bow_data = stemmed_bow_data[:, word_counts > 2]

    stemmed_reduced_embed_vocab = {}
    for w in stemmed_reduced_vocab:
        old_w_embed = [embed_vocab[w_old] for w_old in stemmed_dict[w]]
        if embed_aggregate == 'mean':
            new_w_embed = np.mean(old_w_embed, axis=0)
        elif embed_aggregate == 'first':
            new_w_embed = old_w_embed[0]
        else:
            print('Unknown embedding aggregation')
            break
        stemmed_reduced_embed_vocab[w] = new_w_embed

    return (stemmed_reduced_vocab,
            stemmed_reduced_embed_vocab,
            stemmed_reduced_bow_data)


def get_embedded_data(bow_data, embed_vocab, vocab):
    """Map bag-of-words data to embedded representation."""
    M, V = bow_data.shape
    embed_data = [[] for _ in range(M)]
    for i in range(V):
        for d in range(M):
            if bow_data[d, i] > 0:
                for _ in range(bow_data[d, i]):
                    embed_data[d].append(embed_vocab[vocab[i]])
    return [np.array(embed_doc) for embed_doc in embed_data]


def change_embeddings(vocab, bow_data, embed_path):
    """Change embedding data if vocabulary has been reduced."""
    all_embed_vocab = {}
    with open(embed_path, 'r') as file:
        for line in file.readlines():
            word = line.split(' ')[0]
            embedding = [float(x) for x in line.split(' ')[1:]]
            all_embed_vocab[word] = embedding

    data_embed_vocab = {}
    new_vocab_idx = []
    new_vocab = []
    for i, w in enumerate(vocab):
        if w in all_embed_vocab:
            data_embed_vocab[w] = all_embed_vocab[w]
            new_vocab_idx.append(i)
            new_vocab.append(w)
    #print(new_vocab_idx[-1])
    #print(len(bow_data))
    
    bow_data = bow_data[:, new_vocab_idx]
    return new_vocab, data_embed_vocab, bow_data


def fit_topics(data, embeddings, vocab, K, tpath, ldapath):
    """Fit a topic model to bag-of-words data."""
    if os.path.exists(ldapath):
        model=pickle.load(open(ldapath, "rb"))
    else:
        model = lda.LDA(n_topics=K, n_iter=1500, random_state=1)
        model.fit(data)
        pickle.dump(model, open(ldapath, 'wb'))
    topics = model.topic_word_
    #lda_centers not used?
    #lda_centers = np.matmul(topics, embeddings)
    
    # todo add ITF support by multiplying ITF with topic dist
    
    print('LDA Gibbs topics')
    n_top_words = 20
    top_topic_words = {}
    for i, topic_dist in enumerate(topics):
        topic_words = np.array(vocab)[np.argsort(topic_dist)][:-(n_top_words + 1):-1]
        print('Topic {}: {}'.format(i, ' '.join(topic_words)))
        top_topic_words[i] = topic_words
    print('\n')
    
    topic_proportions = model.doc_topic_
    with open(tpath, "w", encoding="UTF-8") as f:
        for i in range(K):
            f.write(str(i) +"\t"+ re.sub("\n","",str(top_topic_words[i])))
            f.write("\n")

    return topics,  topic_proportions, top_topic_words




def loader(data_path,
           embeddings_path,
           contextual_embeddings,
           raw_data,
           p=1,
           K_lda=70,
           glove_embeddings=True,
           stemming=True,
           n_words_keep = 20, 
           train_test_dataset=False, by_sentence=False):
    """ Load dataset and embeddings from data path."""
    sys.setrecursionlimit(100000)
    print("reclimit")
    print(sys.getrecursionlimit())
    # Will segfault without this line.
    import resource
    resource.setrlimit(resource.RLIMIT_STACK, [0x10000000, resource.RLIM_INFINITY])
    sys.setrecursionlimit(0x100000)
    # Load dataset from data_path
    if data_path =="data/20news":
        vocab, bow_data, y, words  = load_20news()
    else:
        vocab, embed_vocab, bow_data, y, words = load_wmd_data(data_path)
    y = y - 1
    raw_docs= None
    context_emb=None
    # create contextual embeddings using the raw data as an input
    if contextual_embeddings == True:
        if train_test_dataset==False:
            handle= open("data/raw_data/%s_emb.pkl"%os.path.splitext(raw_data)[0],"rb") 
            c_embeddings=pickle.load(handle)
           
        #for raw datasets with train test split  
        '''
        else:
            x=np.load(str(os.path.splitext(raw_data)[0]+"_emb.npy"), allow_pickle=True)
            if os.path.exists(str(os.path.splitext("".join(["" if x=="train_" else x for x in raw_data.partition("train_")]))[0]+"_emb.npy")):
                print("loading already merged dicts")
                c_embeddings=np.load(str(os.path.splitext("".join(["" if x=="train_" else x for x in raw_data.partition("train_")]))[0]+"_emb.npy"),allow_pickle=True)

            elif "train" in raw_data:              
                if os.path.exists("".join(["test" if x=="train" else x for x in raw_data.partition("train")])):
                    if os.path.exists(os.path.splitext("".join(["test" if x=="train" else x for x in raw_data.partition("train")]))[0]+"_emb.npy"):
                        z=np.load(str(os.path.splitext("".join(["test" if x=="train" else x for x in raw_data.partition("train")]))[0]+"_emb.npy"), allow_pickle=True)
                        merged={}
                        print("merging dicts now")
                        last=[]
                        for i in x.item().keys():
                            merged[int(i)] = x.item().get(i)
                            last.append(i)
                        last=int(sorted(last)[-1])+1
                        # merging both contextual embedding files together
                        for i in z.item().keys():
                            merged[int(i+last)] = z.item().get(i)
                        np.save(str(os.path.splitext("".join(["" if x=="train_" else x for x in raw_data.partition("train_")]))[0]+"_emb.npy"),merged)
                        c_embeddings=np.load(str(os.path.splitext("".join(["" if x=="train_" else x for x in raw_data.partition("train_")]))[0]+"_emb.npy"),allow_pickle=True)

                    else:
                        print("does not exist, but will create now:")
                        print(os.path.splitext("".join(["test" if x=="train" else x for x in raw_data.partition("train")]))[0]+"_emb.npy")
                        z_docs, z=map_raw("".join(["test" if x=="train" else x for x in raw_data.partition("train")]), by_sentence)
                        np.save(str(os.path.splitext("".join(["test" if x=="train" else x for x in raw_data.partition("train")]))[0]+"_emb.npy"), z)
                        z=np.load(str(os.path.splitext("".join(["test" if x=="train" else x for x in raw_data.partition("train")]))[0]+"_emb.npy"), allow_pickle=True)
                        with open(str(os.path.splitext("".join(["test" if x=="train" else x for x in raw_data.partition("train")]))[0]+"_proc.csv"),"w", encoding="utf-8") as f:
                            w=csv.writer(f)            
                            for key, val in z_docs.items():
                                w.writerow([key, val])
                        merged={}
                        last=[]
                        for i in x.item().keys():
                            merged[int(i)] = x.item().get(i)
                            last.append(i)
                        last=int(sorted(last)[-1])+1
                        # merging both contextual embedding files together
                        for i in z.item().keys():
                            merged[int(i+last)] = z.item().get(i)
                            #del z.item()[i]
                        np.save(str(os.path.splitext("".join(["" if x=="train_" else x for x in raw_data.partition("train_")]))[0]+"_emb.npy"),merged)
                        c_embeddings=np.load(str(os.path.splitext("".join(["" if x=="train_" else x for x in raw_data.partition("train_")]))[0]+"_emb.npy"),allow_pickle=True)


            elif "test" in raw_data:              
                if os.path.exists("".join(["train" if x=="test" else x for x in raw_data.partition("test")])):
                    if os.path.exists(os.path.splitext("".join(["train" if x=="test" else x for x in raw_data.partition("test")]))[0]+"_emb.npy"):
                        z=np.load(str(os.path.splitext("".join(["train" if x=="test" else x for x in raw_data.partition("test")]))[0]+"_emb.npy"), allow_pickle=True)
                        merged={}
                        last=[]
                        for i in x.item().keys():
                            merged[int(i)] = x.item().get(i)
                            last.append(i)
                        last=int(sorted(last)[-1])+1
                        # merging both contextual embedding files together
                        for i in z.item().keys():
                            merged[int(i+last)] = z.item().get(i)
                            #del z.item()[i]
                        np.save(str(os.path.splitext("".join(["" if x=="test_" else x for x in raw_data.partition("test_")]))[0]+"_emb.npy"),merged)
                        c_embeddings=np.load(str(os.path.splitext("".join(["" if x=="test_" else x for x in raw_data.partition("test_")]))[0]+"_emb.npy"),allow_pickle=True)

                    else:
                        print("does not exist, but will create now:")
                        print(os.path.splitext("".join(["train" if x=="test" else x for x in raw_data.partition("test")]))[0]+"_emb.npy")
                        z_docs, z=map_raw("".join(["train" if x=="test" else x for x in raw_data.partition("test")]), by_sentence)
                        np.save(str(os.path.splitext("".join(["train" if x=="test" else x for x in raw_data.partition("test")]))[0]+"_emb.npy"), z)
                        z=np.load(str(os.path.splitext("".join(["train" if x=="test" else x for x in raw_data.partition("test")]))[0]+"_emb.npy"), allow_pickle=True)
                        with open(str(os.path.splitext("".join(["train" if x=="test" else x for x in raw_data.partition("test")]))[0]+"_proc.csv"),"w", encoding="utf-8") as f:
                            w=csv.writer(f)            
                            for key, val in z_docs.items():
                                w.writerow([key, val])
                        merged={}
                        last=[]
                        for i in x.item().keys():
                            merged[int(i)] = x.item().get(i)
                            last.append(i)
                        last=int(sorted(last)[-1])+1
                        # merging both contextual embedding files together
                        for i in z.item().keys():
                            merged[int(i+last)] = z.item().get(i)
                            #del z.item()[i]
                        np.save(str(os.path.splitext("".join(["" if x=="test_" else x for x in raw_data.partition("test_")]))[0]+"_emb.npy"),merged)
                        c_embeddings=np.load(str(os.path.splitext("".join(["" if x=="test_" else x for x in raw_data.partition("test_")]))[0]+"_emb.npy"),allow_pickle=True)

            else:
                raise("wrong flag selected, no file with train or test prefix")
            # overwrite document length if we merge raw train and test'''
      
    # Use GLOVE word embeddings
    if glove_embeddings:
        vocab, embed_vocab, bow_data = change_embeddings(
            vocab, bow_data, embeddings_path)
    # Reduce vocabulary by removing short words, stop words, and stemming
    if stemming:
        vocab, embed_vocab, bow_data = reduce_vocab(
            bow_data, vocab, embed_vocab, embed_aggregate='mean')

    # Matrix of word embeddings
    embeddings = np.array([embed_vocab[w] for w in vocab])
    '''print(embeddings.shape)
    print(embeddings[0].shape)
    print(type(embeddings))
    print(type(embeddings[0]))
    print(embeddings[0])
    print(depth(embeddings[0]))
    input()'''
    ldapath=str(os.path.splitext(raw_data)[0]+"_lda.pkl")
    tpath=str(os.path.splitext(raw_data)[0]+"_topics.txt")
    topics, topic_proportions, top_topic_words = fit_topics(
        bow_data, embeddings, vocab, K_lda, tpath, ldapath)
 
    cost_embeddings = euclidean_distances(embeddings, embeddings) ** p
    
    cost_topics = np.zeros((topics.shape[0], topics.shape[0]))
    
    
    ## Reduce topics to top-20 words
    if n_words_keep is not None:                                                                                                                                                                                                            
        for k in range(K_lda):
            to_0_idx = np.argsort(-topics[k])[n_words_keep:]
            topics[k][to_0_idx] = 0
    
    # for S-HOTTER
    cost_scontextual = np.zeros((topics.shape[0], topics.shape[0]))        
    # for A-HOTTER
    cost_contextual = np.zeros((topics.shape[0], topics.shape[0]))
    # for M-HOTTER
    cost_mcontextual = np.zeros((topics.shape[0], topics.shape[0]))
    # for MS-HOTTER
    cost_msincontextual = np.zeros((topics.shape[0], topics.shape[0]))
   
  
    for i in range(cost_topics.shape[0]):
        for j in range(i + 1, cost_topics.shape[1]):
            cost_topics[i, j] = sparse_ot(topics[i], topics[j], cost_embeddings)
    cost_topics = cost_topics + cost_topics.T
    
    # for M-HOTTER
    # getting for each topic a set of top documents
  

   
    '''Mapping the contextual embeddings from the BERT Tokenizer 
    to the tokens used by the topic model '''
    if not os.path.exists(str(os.path.splitext(raw_data)[0]+"_con_emb.npy")): 
        print("vocab list length")
        print(len(vocab))
        todo=len(vocab)
        stemmer = SnowballStemmer("english")
        # since the results come in a strange format we have to put it in a dict
        all_embeddings={}
        single_embeddings={}
        m_embeddings={}
        ms_embeddings={}
        #results=[pool.apply_async(map_to_emb, (o,w, c_embeddings, m_topic_words)) for o, w in enumerate(vocab)]
        #output = [p.get() for p in results]
        try:
            x= pre_aggregate(c_embeddings)
            print("now continuing with aggregation")
            c_embeddings=[]
            word_emb = x[0] 
            word_doc= x[1]  
            
            doc_word= x[2]  
            doc_emb= x[3] 
            
            
            
            ''''process for m hotter and t hotter (later in the code t hotter is called ms hotter)'''
            top_documents=defaultdict(list)
            for i, doc in enumerate(topic_proportions):
                prominent_topic=np.max(doc)
                prominent_index=np.argmax(doc)
                top_documents[prominent_index].append([i, prominent_topic])
            second_tier=[]
            # checking if all topics have at least one document that has that topic
            # as a promoninent topic
            for i in range(K_lda):
                try:
                    print(i)
                    print(top_documents[i])
                except KeyError as E:
                    print(E)
                    print(traceback.print_exc())
                    second_tier.append(i)
            # if there is one topic that does not have a document assigned, check all
            # documents for the second most probable topic
            if second_tier:
                #print("found second tier docs")
                #print(second_tier)
            for i, doc in enumerate(topic_proportions):
                    print(doc)
                    prominent_topic=np.sort(doc)[-2]
                    prominent_index=np.argsort(doc)[-2]
                    if prominent_index in second_tier:
                        top_documents[prominent_index].append([i, prominent_topic])
            third_tier=[]
            for i in range(K_lda):
                try:
                    print(top_documents[i])
                except KeyError as E:
                    print(E)
                    third_tier.append(i)
            # if there is one topic that does not have a document assigned, check all
            # documents for the third most probable topic
            if third_tier:
                #print("found third tier docs")
                #print(third_tier)
                #input()
            for i, doc in enumerate(topic_proportions):
                    #print(doc)
                    prominent_topic=np.sort(doc)[-3]
                    prominent_index=np.argsort(doc)[-3]
                    if prominent_index in third_tier:
                        top_documents[prominent_index].append([i, prominent_topic])
            # continue with that as needed...
            '''fourth_tier=[]
            for i in range(0,69):
                try:
                    print(top_documents[i])
                except KeyError as E:
                    print(E)
                    fourth_tier.append(i)
            if fourth_tier:
                print("found fourth tier docs")
                print(fourth_tier)
                input()'''
            m_topic_words=defaultdict(list)
            
            stemmed_word_doc=defaultdict(list)
            for w,d in word_doc.items():
                stemmed_word_doc[stemmer.stem(w)].append(d)
            
            #retrieve documents for the the top words to aggregate for M-HOTTER
            
            
            for t in range(K_lda):
                try:
                    #print(topics[t])
                    doc_list=sorted(top_documents[t], key=lambda x: x[1])
                    #print(doc_list)
                    for w in top_topic_words[t]:
                        if w in stemmed_word_doc.keys():
                            for d in stemmed_word_doc[w]:
                                if d in doc_list:
                                    m_topic_words[w].append(d)
                                
                except Exception as E:
                            print(traceback.print_exc())
                            print(E)
                            print(w)
                            #input()
            np.save("%s_topwords"%raw_data, m_topic_words)    
            
            
            
            x=None
          
          
            for o,w in enumerate(vocab):
                print(str(o)+"/"+str(todo))
                x=map_to_emb(o,w, word_emb, word_doc, doc_word, doc_emb,m_topic_words )
                # x[0] is a word
                # x[1] is the (possibly aggregated) contextual embedding for it
            
                if isinstance(x, list) or isinstance(x, tuple):
                   all_embeddings[x[0]]=x[1]
                   single_embeddings[x[0]]=x[2]
                   m_embeddings[x[0]]=x[3]
                   ms_embeddings[x[0]]=x[4]
        except Exception as e:
            print(e)
            traceback.print_exc()
        #pool.close()
        #pool.join()
        #pool.terminate()
        
  
        #saving this as a numpy array offers compression    
        np.save(str(os.path.splitext(raw_data)[0]+"_con_emb.npy"), all_embeddings)
        np.save(str(os.path.splitext(raw_data)[0]+"_s_emb.npy"), single_embeddings)
        np.save(str(os.path.splitext(raw_data)[0]+"_m_emb.npy"), m_embeddings)
        np.save(str(os.path.splitext(raw_data)[0]+"_ms_emb.npy"), ms_embeddings)
        # we have to load it back because numpy arrays 
        #are accessed differently than dictionaries
        single_embeddings=np.load(str(os.path.splitext(raw_data)[0]+"_s_emb.npy"), allow_pickle=True)
        m_embeddings=np.load(str(os.path.splitext(raw_data)[0]+"_m_emb.npy"), allow_pickle=True)
        ms_embeddings=np.load(str(os.path.splitext(raw_data)[0]+"_ms_emb.npy"), allow_pickle=True)
        all_embeddings=np.load(str(os.path.splitext(raw_data)[0]+"_con_emb.npy"), allow_pickle=True)
    else:
        
        single_embeddings=np.load(str(os.path.splitext(raw_data)[0]+"_s_emb.npy"), allow_pickle=True)
        m_embeddings=np.load(str(os.path.splitext(raw_data)[0]+"_m_emb.npy"), allow_pickle=True)
        ms_embeddings=np.load(str(os.path.splitext(raw_data)[0]+"_ms_emb.npy"), allow_pickle=True)
        all_embeddings=np.load(str(os.path.splitext(raw_data)[0]+"_con_emb.npy"), allow_pickle=True)
    cms_embeddings=np.array([np.array(ms_embeddings.item().get(w)) for w in vocab])
    cm_embeddings=np.array([np.array(m_embeddings.item().get(w)) for w in vocab])
    s_embeddings=np.array([np.array(single_embeddings.item().get(w)) for w in vocab])
    con_embeddings=np.array([np.array(all_embeddings.item().get(w)) for w in vocab])
    # making sure that everything has the same shape
    for i, w in enumerate(con_embeddings):
        #print("shape")
        #print(w.shape)
        if w.shape!=(768,):
            try:
                con_embeddings[i]=w.reshape(768,)
                #print(con_embeddings[i].shape) 
            except ValueError:
                con_embeddings[i]=np.mean(np.asarray(w), axis=0)
                print(con_embeddings[i].shape)
    con_embeddings=np.stack(con_embeddings)
    for i, w in enumerate(s_embeddings):
        if w.shape!=(768,):
            try:
                s_embeddings[i]=w.reshape(768,)
                #print(s_embeddings[i].shape) 
            except ValueError:
                s_embeddings[i]=np.mean(np.asarray(w), axis=0)
                print(s_embeddings[i].shape)
    s_embeddings=np.stack(s_embeddings)
    for i, w in enumerate(cms_embeddings):
        if w.shape!=(768,):
            try:
                cms_embeddings[i]=w.reshape(768,)
                #print(cms_embeddings[i].shape) 
            except ValueError:
                cms_embeddings[i]=np.mean(np.asarray(w), axis=0)
                print(cms_embeddings[i].shape)
    cms_embeddings=np.stack(cms_embeddings)
    for i, w in enumerate(cm_embeddings):
        if w.shape!=(768,):
            try:
                cm_embeddings[i]=w.reshape(768,)
                #print(cm_embeddings[i].shape) 
            except ValueError:
                cm_embeddings[i]=np.mean(np.asarray(w), axis=0)
                print(cm_embeddings[i].shape)
    cm_embeddings=np.stack(cm_embeddings)
    print(len(topics))            
    print(len(vocab))
    print(len(embeddings))
    print(len(con_embeddings))
    print(len(cm_embeddings))
    print(len(cms_embeddings))
    print(len(s_embeddings))
   
   
        
            
    # A-HOTTER        
    cost_c_embeddings = euclidean_distances(con_embeddings, con_embeddings) ** p
    # M-HOTTER
    cost_cm_embeddings = euclidean_distances(cm_embeddings, cm_embeddings) ** p
    # MS-HOTTER
    cost_cms_embeddings = euclidean_distances(cms_embeddings, cms_embeddings) ** p
    # S-HOTTER
    cost_s_embeddings = euclidean_distances(s_embeddings, s_embeddings) ** p
    
    
    #using the document topic proportions to obtain representative contextual embeddings per topic
    for i in range(cost_contextual.shape[0]):
        for j in range(i + 1, cost_contextual.shape[1]):
            cost_contextual[i, j] = sparse_ot(topics[i], topics[j], cost_c_embeddings)
            cost_mcontextual[i, j] = sparse_ot(topics[i], topics[j], cost_cm_embeddings)
            cost_scontextual[i, j] = sparse_ot(topics[i], topics[j], cost_s_embeddings)
            cost_msincontextual[i, j] = sparse_ot(topics[i], topics[j], cost_cms_embeddings)

    cost_contextual = cost_contextual + cost_contextual.T
    cost_mcontextual = cost_mcontextual + cost_mcontextual.T
    cost_scontextual = cost_scontextual + cost_scontextual.T
    cost_msincontextual = cost_msincontextual + cost_msincontextual.T
    
    out = {'X': bow_data, 'y': y,
           'embeddings': embeddings,
           'topics': topics, 'proportions': topic_proportions,
           'cost_E': cost_embeddings, 'cost_T': cost_topics, 'raw_docs':raw_docs, 'contextual_emb':context_emb, 'cost_CT':cost_contextual, 'cost_MCT':cost_mcontextual, 'cost_MSCT':cost_msincontextual, 'cost_SCT':cost_scontextual}

    return out


## 🔥 5. HOTT(ER) Distance +  Baseline Calculation

In [6]:

# p=1 is for W1 metric, p=2 for W2
p = 1
data = loader(data_path + data_name, embeddings_path, contextual_embeddings=True, raw_data=raw_data_name, p=p,K_lda=70,glove_embeddings=True, stemming=True,n_words_keep=20, train_test_dataset=train_test_dataset, by_sentence=by_sentence)
cost_E = data['cost_E']
#print(np.argwhere(np.isnan(cost_E)))
#input()
cost_T = data['cost_T']

bow_data, y = data['X'], data['y']
topic_proportions = data['proportions']

seed = 0
bow_train, bow_test, topic_train, topic_test, y_train, y_test = train_test_split(bow_data, topic_proportions, y, random_state=seed)

# Pick a method among RWMD, WMD, WMD-T20, HOTT, HOFTT, A-HOTTER, S-HOTTER and M-HOTTER

methods = {'S-HOTTER': hott.hott,
           'A-HOTTER': hott.hott,
           'M-HOTTER': hott.hott,
           'T-HOTTER': hott.hott,
           'HOTT': hott.hott,
           'HOFTT': hott.hoftt,
           'RWMD': distances.rwmd,
           'WMD-T20': lambda p, q, C: distances.wmd(p, q, C, truncate=20),
           'WMD': distances.wmd}
    
for method in methods.keys():
    
    t_s = time.time()
    # Get train/test data representation and transport cost
    if method in ['HOTT', 'HOFTT']:
        # If method is HOTT or HOFTT train LDA and compute topic-topic transport cost
        X_train, X_test = topic_train, topic_test
        C = data['cost_T']
    elif method in ['A-HOTTER']:
        # If method is HOTTER do the same as for HOTT except for taking contextual costs from averaged tier 1 documents
        X_train, X_test = topic_train, topic_test
        C = data['cost_CT']
    elif method in ['S-HOTTER']:
        # If method is HOTTER do the same as for HOTT except for taking contextual costs from averaged tier 1 documents
        X_train, X_test = topic_train, topic_test
        C = data['cost_SCT']
    elif method in ['M-HOTTER']:
        # If method is HOTTER do the same as for HOTT except for taking contextual costs from the maximum probability tier 1 doc
        X_train, X_test = topic_train, topic_test
        C = data['cost_MCT']
    elif method in ['T-HOTTER']:
        # If method is HOTTER do the same as for HOTT except for taking contextual costs from the maximum probability tier 1 doc
        X_train, X_test = topic_train, topic_test
        C = data['cost_MSCT']
    else:
        # Normalize BOW and compute word-word transport cost
        X_train, X_test = normalize(bow_train, 'l1'), normalize(bow_test, 'l1')
        C = data['cost_E']
    
    # Compute test error
    test_error = knn(X_train, X_test, y_train, y_test, methods[method], C, n_neighbors=7)
    print(method + ' test error is %f; took %.2f seconds' % (test_error, time.time()-t_s))

# Done!

reclimit
100000
10102
737


INFO:lda:n_documents: 737
INFO:lda:vocab_size: 3657
INFO:lda:n_words: 102776
INFO:lda:n_topics: 70
INFO:lda:n_iter: 1500
INFO:lda:<0> log likelihood: -1432582
INFO:lda:<10> log likelihood: -850644
INFO:lda:<20> log likelihood: -814569
INFO:lda:<30> log likelihood: -800267
INFO:lda:<40> log likelihood: -794318
INFO:lda:<50> log likelihood: -788032
INFO:lda:<60> log likelihood: -785772
INFO:lda:<70> log likelihood: -783560
INFO:lda:<80> log likelihood: -781132
INFO:lda:<90> log likelihood: -780450
INFO:lda:<100> log likelihood: -779637
INFO:lda:<110> log likelihood: -777405
INFO:lda:<120> log likelihood: -777171
INFO:lda:<130> log likelihood: -775959
INFO:lda:<140> log likelihood: -775654
INFO:lda:<150> log likelihood: -775088
INFO:lda:<160> log likelihood: -774323
INFO:lda:<170> log likelihood: -773964
INFO:lda:<180> log likelihood: -774161
INFO:lda:<190> log likelihood: -773395
INFO:lda:<200> log likelihood: -772434
INFO:lda:<210> log likelihood: -771497
INFO:lda:<220> log likelihood: 

LDA Gibbs topics
Topic 0: test day wicket bowl bat open one run score seri batsman inning michael centuri left team man set skipper start
Topic 1: year roddick cup beat spain play win davi doubl singl andi carlo open clay surfac nadal victori guy day court
Topic 2: goal score win half match top place premiership leagu great charlton paid conced cup back champion earn striker one spot
Topic 3: day make time lot posit thing peopl come made part put plan decis want happen point happi respect month ask
Topic 4: cont jone perform take enhanc steroid alleg white posit agenc charg investig anti world dope televis wednesday marion victor american
Topic 5: year time season old ad join good return appear made left play four talent moor first kent injur choic domest
Topic 6: olymp athlet holm britain kelli athen birmingham gold lewi garden franci doubl relay medal green compet british event campbel track
Topic 7: match world tsunami player rais hit chris said star fund earli asian game contribut 

vocab list length
3657
0\737
1\737
2\737
3\737
4\737
5\737
6\737
7\737
8\737
9\737
10\737
11\737
12\737
13\737
14\737
15\737
16\737
17\737
18\737
19\737
20\737
21\737
22\737
23\737
24\737
25\737
26\737
27\737
28\737
29\737
30\737
31\737
32\737
33\737
34\737
35\737
36\737
37\737
38\737
39\737
40\737
41\737
42\737
43\737
44\737
45\737
46\737
47\737
48\737
49\737
50\737
51\737
52\737
53\737
54\737
55\737
56\737
57\737
58\737
59\737
60\737
61\737
62\737
63\737
64\737
65\737
66\737
67\737
68\737
69\737
70\737
71\737
72\737
73\737
74\737
75\737
76\737
77\737
78\737
79\737
80\737
81\737
82\737
83\737
84\737
85\737
86\737
87\737
88\737
89\737
90\737
91\737
92\737
93\737
94\737
95\737
96\737
97\737
98\737
99\737
100\737
101\737
102\737
103\737
104\737
105\737
106\737
107\737
108\737
109\737
110\737
111\737
112\737
113\737
114\737
115\737
116\737
117\737
118\737
119\737
120\737
121\737
122\737
123\737
124\737
125\737
126\737
127\737
128\737
129\737
130\737
131\737
132\737
133\737
134\737
135\737

[0.00097087 0.00097087 0.00097087 0.03980583 0.00097087 0.00097087
 0.00097087 0.00097087 0.01067961 0.00097087 0.00097087 0.00097087
 0.00097087 0.00097087 0.00097087 0.0592233  0.02038835 0.00097087
 0.00097087 0.01067961 0.01067961 0.01067961 0.1368932  0.00097087
 0.00097087 0.00097087 0.00097087 0.00097087 0.00097087 0.00097087
 0.00097087 0.00097087 0.00097087 0.09805825 0.00097087 0.00097087
 0.01067961 0.03980583 0.00097087 0.23398058 0.02038835 0.00097087
 0.01067961 0.01067961 0.02038835 0.00097087 0.00097087 0.00097087
 0.03980583 0.00097087 0.00097087 0.00097087 0.03009709 0.00097087
 0.00097087 0.00097087 0.00097087 0.00097087 0.00097087 0.00097087
 0.00097087 0.00097087 0.00097087 0.03980583 0.00097087 0.03980583
 0.01067961 0.04951456 0.00097087 0.00097087]
[0.00071942 0.01510791 0.01510791 0.00071942 0.00071942 0.00071942
 0.00071942 0.00071942 0.00071942 0.00071942 0.07985612 0.00071942
 0.00071942 0.00071942 0.00071942 0.00071942 0.02230216 0.00071942
 0.01510791 0.02

...

2938/3657
floyd
13533
2939/3657
blush
13533
2940/3657
palm
13533
2941/3657
offsid
13533
2942/3657
sink
13533
2943/3657
pen
13533
2944/3657
fish
13533
2945/3657
dunde
13533
2946/3657
aberdeen
13533
2947/3657
richi
13533
2948/3657
stevi
13533
2949/3657
crawford
13533
2950/3657
bullock
13533
2951/3657
robson
13533
2952/3657
tap
13533
2953/3657
onrush
13533
2954/3657
lob
13533
2955/3657
samuel
13533
2956/3657
kerr
13533
2957/3657
kenneth
13533
2958/3657
hart
13533
2959/3657
diamond
13533
2960/3657
clyde
13533
2961/3657
celtic
13533
2962/3657
brush
13533
2963/3657
slid
13533
2964/3657
bellami
13533
2965/3657
blown
13533
2966/3657
sheridan
13533
2967/3657
scenario
13533
2968/3657
flare
13533
2969/3657
intervent
13533
2970/3657
unmark
13533
2971/3657
culmin
13533
2972/3657
burn
13533
2973/3657
gibson
13533
2974/3657
lennon
13533
2975/3657
livingston
13533
2976/3657
simmon
13533
2977/3657
lifelin
13533
2978/3657
eric
13533
2979/3657
dair
13533
2980/3657
gordon
13533
2981/3657
webster
13533
298

3275/3657
manuel
13533
3276/3657
son
13533
3277/3657
mexican
13533
3278/3657
shark
13533
3279/3657
rubber
13533
3280/3657
stamp
13533
3281/3657
wood
13533
3282/3657
millwal
13533
3283/3657
mutu
13533
3284/3657
cocain
13533
3285/3657
argentin
13533
3286/3657
edu
13533
3287/3657
destroy
13533
3288/3657
mirror
13533
3289/3657
regret
13533
3290/3657
privat
13533
3291/3657
artifici
13533
3292/3657
swindon
13533
3293/3657
wigan
13533
3294/3657
milton
13533
3295/3657
anelka
13533
3296/3657
haunt
13533
3297/3657
rift
13533
3298/3657
bill
13533
3299/3657
mexico
13533
3300/3657
strachan
13533
3301/3657
ice
13533
3302/3657
cake
13533
3303/3657
laugh
13533
3304/3657
tevez
13533
3305/3657
boca
13533
3306/3657
argentina
13533
3307/3657
brightest
13533
3308/3657
bueno
13533
3309/3657
passion
13533
3310/3657
copa
13533
3311/3657
feint
13533
3312/3657
shoot
13533
3313/3657
miser
13533
3314/3657
hardest
13533
3315/3657
ghana
13533
3316/3657
off
13533
3317/3657
blight
13533
3318/3657
cartilag
13533
3319/

3637/3657
volvo
13533
3638/3657
hardcourt
13533
3639/3657
chela
13533
3640/3657
lisa
13533
3641/3657
ephedrin
13533
3642/3657
exhibit
13533
3643/3657
medicin
13533
3644/3657
bailey
13533
3645/3657
lawn
13533
3646/3657
memphi
13533
3647/3657
contamin
13533
3648/3657
gaston
13533
3649/3657
manga
13533
3650/3657
unassail
13533
3651/3657
sharapova
13533
3652/3657
houston
13533
3653/3657
hip
13533
3654/3657
mario
13533
3655/3657
crosscourt
13533
3656/3657
roch
13533
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
s

(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape
(768,)
shape

S-HOTTER test error is 0.027027; took 7.36 seconds
A-HOTTER test error is 0.021622; took 7.51 seconds
M-HOTTER test error is 0.021622; took 7.49 seconds
T-HOTTER test error is 0.016216; took 7.43 seconds
HOTT test error is 0.021622; took 7.47 seconds
HOFTT test error is 0.021622; took 31.48 seconds
RWMD test error is 0.032432; took 15.68 seconds
WMD-T20 test error is 0.048649; took 22.85 seconds
WMD test error is 0.027027; took 96.43 seconds
